In [2]:
import sympy as sp

def delta_op(i, j, size = 3):
    """
    计算增量
    [
        -1, 0, 0,
        0, 0, 0,
        1, 0, 0
    ]
    相当于:
      d a_i = - a_i
      d a_j = a_i
    """
    
    delta = sp.zeros(size, size)
    delta[i, i] = -1
    delta[j, i] = 1
    
    return delta

def add_op(i, j, x, b):
    size = x.shape[0]
    try_op = sp.eye(size, size) + delta_op(i, j, size)
    try_add = try_op * x

    overflow = try_add - b
    overflow_guard = overflow.applyfunc(lambda x: sp.Max(x, 0))

    compensate = delta_op(j, i, size) * overflow_guard

    return try_add + compensate

In [17]:
display(delta_op(0, 2))
display(delta_op(2, 0))
display(delta_op(2, 0).T)
display(delta_op(0, 2) == delta_op(2, 0).T)

Matrix([
[-1, 0, 0],
[ 0, 0, 0],
[ 1, 0, 0]])

Matrix([
[0, 0,  1],
[0, 0,  0],
[0, 0, -1]])

Matrix([
[0, 0,  0],
[0, 0,  0],
[1, 0, -1]])

False

In [3]:
x = sp.Matrix([[4, 9, 0]]).T
b = sp.Matrix([[4, 9, 9]]).T
x_new = add_op(0, 2, x, b)
print(x_new)
x_new_new = add_op(1, 2, x_new, b)
print(x_new_new)

print(add_op(0, 1, sp.Matrix([[4, 0, 9]]).T, b))

Matrix([[0], [9], [4]])
Matrix([[0], [4], [9]])
Matrix([[0], [4], [9]])


In [4]:
print(x == sp.Matrix([[4, 9, 0]]).T)
print(x == sp.Matrix([[4, 9, 1]]).T)
x.shape[0]
print(min(x.col(0).tolist()))
print(sum(x))

True
False
[0]
13


In [5]:
"""
还支持倒出去, 倒掉最少的那个元素
"""

def drop_op(x):
    size = x.shape[0]
    x.col(0)
    min_val = -1
    min_i = -1
    for i in range(size):
        if min_i < 0:
            min_i = i
            min_val = x[i, 0]
            continue
        if x[i, 0] < min_val and x[i, 0] > 0:
            min_i = i
            min_val = x[i, 0]
    x_new = x.copy()
    x_new[min_i, 0] = 0
    return x_new
print(drop_op(sp.Matrix([[4, 9, 0]]).T))

Matrix([[0], [9], [0]])


In [6]:
class Solver:
    def __init__(self, x0, b, final_cond, size_cond):
        self.size = x0.shape[0]
        self.b = b
        self.x0 = x0
        self.id = 0
        self.store_value = {
            self.id: x0
        }
        self.graph = {
        }
        self.final_cond = final_cond
        self.finds = []
        self.size_cond = size_cond

    def op(self, i, j, x): return add_op(i, j, x, self.b)
    
    def find_graph(self, x):
        for (id, value) in self.store_value.items():
            if x == value:
                return id
        return -1
    
    def set_graph(self, dot1, dot2, op):
        if dot1 not in self.graph:
            self.graph[dot1] = {}
        self.graph[dot1][dot2] = op
    
    def new_id(self): 
        self.id += 1
        return self.id

    def search(self, x_prev = 0, drop_num = 0):
        if not self.size_cond(self.store_value[x_prev]):
            return
        ops = []
        for i in range(self.size):
            for j in range(self.size):
                if i == j: continue
                x_new = self.op(i, j, self.store_value[x_prev])
                ops.append((x_new, (i, j, drop_num)))
        if drop_num <= 2:
            drop_num += 1
            ops.append((drop_op(self.store_value[x_prev]), (-1, -1, drop_num)))
        
        for (x_new, op) in ops:
            (i, j, drop_num) = op
            if (id := self.find_graph(x_new)) >= 0:
                if not id == x_prev:
                    self.set_graph(x_prev, id, (i, j) if i >= 0 else "drop")
                continue
            else:
                id = self.new_id()
                self.store_value[self.id] = x_new
            self.set_graph(x_prev, id, (i, j) if i >= 0 else "drop")
            if self.final_cond(x_new):
                self.finds.append(id)
                continue
            self.search(id, drop_num)
    
                

solver = Solver(
    sp.Matrix([[4, 9, 0]]).T, 
    sp.Matrix([[4, 9, 9]]).T, 
    lambda x: x[0] == 6 or x[1] == 6 or x[2] == 6,
    lambda x: sum(x) >= 6
)

solver.search()

print(solver.graph)

print(solver.finds)

{0: {1: (0, 2), 7: (1, 2), 14: 'drop'}, 1: {2: (1, 0), 6: (1, 2), 0: (2, 0)}, 2: {1: (0, 1), 3: (0, 2), 7: (1, 2), 0: (2, 1), 16: 'drop'}, 3: {4: (1, 0), 6: (1, 2), 2: (2, 0), 1: (2, 1)}, 4: {3: (0, 1), 5: (0, 2), 7: (1, 2), 0: (2, 1), 41: 'drop'}, 5: {6: (0, 1), 7: (1, 0), 4: (2, 0), 32: (2, 1), 40: 'drop'}, 6: {7: (1, 0), 29: (2, 0), 1: (2, 1)}, 7: {6: (0, 1), 0: (2, 1), 8: 'drop'}, 8: {9: (2, 0), 14: (2, 1)}, 9: {10: (0, 1), 8: (0, 2), 15: (2, 1), 28: 'drop'}, 10: {9: (1, 0), 8: (1, 2), 11: (2, 0), 14: (2, 1)}, 11: {12: (0, 1), 10: (0, 2), 9: (1, 2), 15: (2, 1), 23: 'drop'}, 12: {11: (1, 0), 8: (1, 2), 13: (2, 0), 14: (2, 1)}, 13: {14: (0, 1), 12: (0, 2), 15: (1, 0), 19: (1, 2), 24: 'drop'}, 14: {15: (1, 0), 8: (1, 2)}, 15: {14: (0, 1), 16: (0, 2), 9: (1, 2), 27: 'drop'}, 16: {17: (1, 0), 8: (1, 2), 15: (2, 0), 14: (2, 1)}, 17: {16: (0, 1), 18: (0, 2), 9: (1, 2), 15: (2, 1), 21: 'drop'}, 18: {19: (1, 0), 8: (1, 2), 17: (2, 0), 14: (2, 1)}, 19: {18: (0, 1), 8: (0, 2), 9: (2, 0), 13: 

In [9]:
import networkx as nx
import matplotlib.pyplot as plt

# 创建一个有向图
G = nx.DiGraph()

# 添加节点和边
for node, neighbors in solver.graph.items():
    for neighbor, op in neighbors.items():
        # 添加边
        G.add_edge(node, neighbor, op=op)
        # 设置节点的标签
        G.nodes[node]['label'] = f"{node}\n{solver.store_value[node].T.tolist()[0]}"
        G.nodes[neighbor]['label'] = f"{neighbor}\n{solver.store_value[neighbor].T.tolist()[0]}"

# 设置绘图布局
pos = nx.bfs_layout(G, 0)

# 创建一个较大的画布
plt.figure(figsize=(40, 40), dpi=400)  # 设置画布大小和分辨率

# 绘制节点
nx.draw_networkx_nodes(G, pos, node_size=3000, node_color='lightblue', alpha=0.8)

# 高亮起点和终点
nx.draw_networkx_nodes(G, pos, nodelist=[0], node_size=3000, node_color="tab:red", alpha=0.8)
for find in solver.finds:
    nx.draw_networkx_nodes(G, pos, nodelist=[find], node_size=3000, node_color="tab:green", alpha=0.8)

# 绘制边
nx.draw_networkx_edges(G, pos, arrowstyle='-', arrowsize=30, edge_color='gray', width=2)

# 绘制节点标签
labels = nx.get_node_attributes(G, 'label')
nx.draw_networkx_labels(G, pos, labels=labels, font_size=14, font_color='black', font_family='sans-serif')


# shortest path
shortest_path = {}
for find in solver.finds:
    path = nx.shortest_path(G, 0, find)
    shortest_path[find] = path

# 绘制最短路径
colors = [
    'blue', 'red', 'cyan'
]
for find, path in shortest_path.items():
    edges = [(path[i], path[i + 1]) for i in range(len(path) - 1)]
    # random color
    color = colors.pop()
    nx.draw_networkx_edges(G, pos, edgelist=edges, edge_color=color, width=2)


# 绘制边的标签（可选）
edge_labels = nx.get_edge_attributes(G, 'op')
nx.draw_networkx_edge_labels(G, pos, edge_labels=edge_labels, font_color='blue', font_size=12)


# 关闭坐标轴
plt.axis('off')

# 保存为矢量图文件
plt.savefig("graph.svg", format="svg")  # 保存为 SVG 格式的矢量图

# 保存为位图文件 (PNG) - 高分辨率
plt.savefig("graph.png", format="png", dpi=300, bbox_inches="tight")

# 显示图形
plt.show()
